# S01.E04 - **Elemental Insights: Pokémon Type and it's Base Stats**
by **@caesarmario** /// <a href="https://linktr.ee/caesarmario_">https://linktr.ee/caesarmario_</a>

## 1. | Importing Libraries

In [1]:
# --- Libraries for 'Secret Sauce' ---
import sys
from IPython.display import display, HTML, Javascript

# --- 'Secret Sauce' Variables ---
""" Change Variables ~! HERE !~ """
project_date = "20240304"
local_path = "config_data_slices"

# ---'Secret Sauce' Function ---
def apply_config_file_data_slices(local_path, project_date):
    sys.path.append(f"{local_path}/{project_date}/")
    
# --- Apply Function & Import Config File ---
apply_config_file_data_slices(local_path, project_date)
from config_file import *

In [2]:
# --- Installing and Importing Libraries ---
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import matplotlib.patheffects as path_effects
import seaborn as sns
import urllib
import requests
import roman
import glob
import time

from tqdm.auto import tqdm
from PIL import Image
from highlight_text import fig_text, ax_text
from datetime import datetime

## 2. | Countmap Pokémon Type

### 2.1 | Dataframes

In [3]:
# --- Func: Process Dataframe ---
def process_df(df, gen):
    df.drop(["Ndex", "MS"], axis=1, inplace=True)
    df.rename(columns={"PokÃ©mon": "pokemon_name", "Type": "type_1", "Type.1": "type_2"}, inplace=True)
    df = df.reset_index(drop=True)
    df["gen"] = gen
    
    return df

# --- Getting Data ---
bulbapedia_url = "https://bulbapedia.bulbagarden.net/wiki/List_of_Pok%C3%A9mon_by_National_Pok%C3%A9dex_number"
req = requests.get(bulbapedia_url)

# --- Variables ---
i = 1

# --- Dataframes ---
df_full = pd.DataFrame()
while i < 10:
    df_temp = pd.read_html(req.content)[i]
    df_temp = process_df(df=df_temp, gen=i)
    df_full = pd.concat([df_full, df_temp], ignore_index = True)
    i += 1
    
# --- Showing Sample Data ---
df_full.sample(7)

pokemon_name    type_1  type_2  gen
55                   Venomoth       Bug  Poison    1
1146                 Arctibax    Dragon     Ice    9
1016                Arctovish     Water     Ice    8
1071                   Dolliv     Grass  Normal    9
979   Toxtricity Low Key Form  Electric  Poison    8
608                  Leavanny       Bug   Grass    5
379                   Seviper    Poison  Poison    3

### 2.2 | Variables

In [4]:
# --- Variables ---
img_size = 0.02
logo_size = 0.08
wm_size = 0.1
margins_type = 0.006
folder_path_s01e04 = "s01e04_png"
png_name1_s01e04 = "data_slices_s01e04_pokemontypecount"

# --- Figure & Highlight Props ---
heatmap_kws = dict(fontsize=6, fontname=font_alt)
patches_prop = dict(fontsize=5, weight=600, horizontalalignment='center', verticalalignment='center', fontname=font_alt)
bar_type = dict(color=color_grad[2], linewidth=0)
xy_label = dict(fontsize=8, weight="bold", fontname=font_main)
image_ax = dict(textcoords="offset points", size=6, fontname=font_alt)
fig_text_prop = dict(ha="left", va="bottom")
tick_params = dict(length=2, width=0.5, color=color_line)
subtitle_highlight_prop = [
    {"color": color_grad[1], "weight": "bold", "font": font_alt}
    , {"color": color_grad[1], "weight": "bold", "font": font_alt}
    , {"color": color_grad[4], "weight": "bold", "font": font_alt}
]
sources_highlight_prop = [
    {"font": font_main, "weight": "bold", "style": "normal", "fontsize": 4.5}
]

### 2.3 | Functions

In [5]:
# --- Func: Processing Pokémon Type Dataframe ---
def process_type_dfs(df, type:str, type_list):
    df_type = pd.DataFrame(df.groupby([type]).size().reset_index(name='total') \
                          .set_index(type).reindex(index=type_list).fillna(0) \
                          .reset_index())
    return df_type

In [6]:
# --- Func: Creating Countmap Figure ---
def main_countmap(ax, df):
    
    # --- Count Map ---
    sns.heatmap(df[type_list].reindex(type_list), annot=True, cbar=False, linewidth=1.2, linecolor=face_color
                , edgecolor="none", cmap=color_map, annot_kws=heatmap_kws, xticklabels=False, yticklabels=False, ax=ax)
    
    # XY Labels & Ticks
    ax.set_xlabel("Type 2\n\n\n\n\n", **xy_label)
    ax.xaxis.set_label_position('top') 
    ax.set_ylabel("Type 1\n\n\n\n\n", **xy_label)

In [7]:
# --- Func: Creating Barchart of Type 1 Figure ---
def type1_barchart(ax, df):
    
    # --- Type 1: Bar Horizontal ---
    ax.barh(df['type_1'], df['total'], **bar_type)
    ax.margins(y=margins_type)
    ax.tick_params(axis="x", labelsize=4, top=True, labeltop=True, bottom=False, labelbottom=False, **tick_params)
    ax.set_yticks([])
    ax.set_xticks(ticks=list(np.arange(0, 170, 20)))
    ax.set_xticklabels(labels=[str(x) for x in ax.get_xticks()])
    ax.grid(False)
    for spine in ax.spines.values(): spine.set_color('None')
    for rect in ax.patches:
        width, height = rect.get_width(), rect.get_height()
        x, y = rect.get_xy()
        height_loc = y+height/2
        if width < 20:
            width_loc = x+width+10
            color_patches = "black"
        else:
            width_loc = x+width/2
            color_patches = "white"
        ax.text(width_loc, height_loc, '{:.0f}'.format(width), color=color_patches, **patches_prop)

In [8]:
# --- Func: Creating Barchart of Type 2 Figure ---
def type2_barchart(ax, df):
    
    # --- Type 2: Bar Horizontal ---
    ax.bar(df['type_2'], df['total'], **bar_type)
    ax.margins(x=margins_type)
    ax.tick_params(axis="y", labelsize=4, left=True, **tick_params)
    ax.set_xticks([])
    ax.set_yticks(ticks=list(np.arange(0, -170, -20)))
    ax.set_yticklabels(labels=[str(round(abs(x))) for x in ax.get_yticks()])
    ax.grid(False)
    for spine in ax.spines.values(): spine.set_color('None')
    for rect in ax.patches:
        width, height = rect.get_width(), rect.get_height()
        x, y = rect.get_xy()
        width_loc = x+width/2
        if round(abs(height)) < 20:
            height_loc = y+height-10
            color_patches = "black"
        else:
            height_loc = y+height/2
            color_patches = "white"
        ax.text(width_loc, height_loc, '{:.0f}'.format(round(abs(height))), color=color_patches, **patches_prop)

In [9]:
# --- Func: Generating Complete Figure ---
def countmap_figure(df, gen):

    # --- Dataframe ---
    # Filter dataframe based on generation & provide roman number for subtitle
    if gen != 0:
        df = df.loc[df['gen'] == gen]
        gen_num_roman = roman.toRoman(gen)
    else:
        gen = "full"
        gen_num_roman = "I to IX"

    # Pivot Dataframe
    df_pivot = df.pivot_table(index="type_1", columns="type_2", aggfunc="size")
    
    # Checking if there are missing rows & columns on the pivot table
    for type in type_list:
        if type not in df_pivot.axes[1]:
            df_pivot[type] = np.nan
        if type not in df_pivot.axes[0]:
            df_pivot.loc[type] = pd.Series(dtype='float64')
            
    df_pivot = df_pivot[type_list].reindex(type_list)

    # Type Dataframes
    data_type1 = process_type_dfs(df=df, type="type_1", type_list=type_list[::-1])

    data_type2 = process_type_dfs(df=df, type="type_2", type_list=type_list)
    data_type2['total'] = data_type2['total'] * -1
    
    # --- Figure Size ---
    fig, ((ax_main, ax_type1), (ax_type2, ax_empty)) = plt.subplots(figsize=(9, 9), nrows=2, ncols=2, sharex=False, sharey=False
                                                                    , gridspec_kw={'height_ratios': [5, 1], 'width_ratios': [9, 2]})
    fig.subplots_adjust(wspace=0.05, hspace=0.05)
    
    # --- Count Map ---
    main_countmap(ax=ax_main, df=df_pivot)

    # --- Type 1: Bar Horizontal ---
    type1_barchart(ax=ax_type1, df=data_type1)

    # --- Type 2: Bar Horizontal ---
    type2_barchart(ax=ax_type2, df=data_type2)

    # --- Empty Subplot ---
    ax_empty.axis("off")

    # --- Countmap Labels ---
    for index in df_icon_url.index:

        # Icon Image
        png_icon = df_icon_url['icon_url_blk'].iloc[index]
        poke_icon = Image.open(urllib.request.urlopen(f"{poke_url}{png_icon}.png")).convert("LA")

        # Label Y Axis
        y_crds = round(0.853-(index*0.0347), 4)
        image_axs_y = fig.add_axes([0.095, y_crds, img_size, img_size], anchor="C")
        image_axs_y.imshow(poke_icon)
        image_axs_y.axis("off")
        image_axs_y.annotate(xy=(0, 0), xytext=(-2.5, -6.2), ha="right", va="center"
                             , text=f"{df_icon_url['icon'].iloc[index]}", **image_ax)

        # Label X Axis
        x_crds = round(0.132+(index*0.0344), 4)
        image_axs_x = fig.add_axes([x_crds, 0.89, img_size, img_size], anchor="C")
        image_axs_x.imshow(poke_icon)
        image_axs_x.axis("off")
        image_axs_x.annotate(xy=(0, 0), xytext=(10, 13), ha="right", va="center", rotation=-45
                             , text=f"{df_icon_url['icon'].iloc[index]}", **image_ax)

    # --- Image Logo ---
    # Logo
    logo_ax = fig.add_axes([0.8, 0.96, logo_size, logo_size], fc="None")
    logo_ax.imshow(data_slices_logo)
    logo_ax.axis("off")

    # Watermark
    wm_ax = fig.add_axes([0.43, -0.03, wm_size, wm_size], fc="None")
    wm_ax.imshow(data_slices_wm)
    wm_ax.axis("off")
    
    # --- Figure Texts ---
    # Title
    fig_text(s="Elemental Insights: A Heatmap of Pokémon Types", x=0.125, y=0.995, fontsize=14, weight="bold", **fig_text_prop)
        
    # Subtitle
    fig_text(s=f"Visualizing the <Pokémon type numbers> from <Generation {gen_num_roman}> | Data Scraped from <Bulbapedia>", x=0.125, y=0.98
             , fontsize=7, font=font_alt, highlight_textprops=subtitle_highlight_prop, **fig_text_prop)
        
    # References
    fig_text(s="""
    <Sources & Inspiration:>
    ∙ https://bulbapedia.bulbagarden.net/wiki/List_of_Pok%C3%A9mon_by_National_Pok%C3%A9dex_number
    ∙ https://www.reddit.com/r/dataisbeautiful/comments/9u1ax9/every_combination_of_pokemon_type_oc/
    ∙ https://github.com/duiker101/pokemon-type-svg-icons/tree/master
    ∙ https://stackoverflow.com/questions/64709205/how-to-improve-beautiful-soup-webscrape-loop
    ∙ https://www.kaggle.com/code/subinium/kaggle-2020-visualization-analysis
    """, x=0.065, y=-0.015, fontsize=4, font=font_alt, style="italic", highlight_textprops=sources_highlight_prop, **fig_text_prop)
    
    # --- Finalizing Figure ---
    plt.savefig(f"{folder_path_s01e04}/countmap/{png_name1_s01e04}_gen{gen}.png"
                , dpi=figure_dpi_hd, bbox_inches="tight", edgecolor="none", transparent=False)
    plt.close(fig);

### 2.4 | Generating Countmap Figures & GIFs

In [10]:
# --- Generating Countmap Figures ---
for gen in tqdm(range(0, 10, 1), desc="🔃🔢 Generating Countmap Figure..."):
    countmap_figure(df=df_full, gen=gen)
    time.sleep(7) # Prevent timeout when getting icons

🔃🔢 Generating Countmap Figure...: 100%|██████████| 10/10 [04:44<00:00, 28.41s/it]


In [11]:
# --- Converting to GIFs ---
# Variables
frames = []

# List Images/Frames
imgs = glob.glob(f"{folder_path_s01e04}/countmap/*.png")
imgs = imgs[-1:] + imgs[:-1]
for img in imgs:
    new_frame = Image.open(img)
    frames.append(new_frame)

# Save to GIFs
frames[0].save(f"{folder_path_s01e04}/countmap/{png_name1_s01e04}.gif", format="GIF"
               , append_images=frames[1:], save_all=True, duration=1200, loop=0)

## 3. | Spiderplot Average Pokémon Base Stats

### 3.1 | Dataframes

In [12]:
# --- Func: Process Dataframe ---
def process_df(df):
    df[["Type 1", "Type 2"]] = df["Type"].str.split(" ", n=1, expand=True)
    df.drop(["#", "Name", "Type"], axis=1, inplace=True)
    
    return df
    
# --- Getting Data ---
pokemondb_url = "https://pokemondb.net/pokedex/all"
req = requests.get(pokemondb_url)

# --- Dataframe ---
df_stats = pd.read_html(req.content)[0]
df_stats = process_df(df=df_stats)

# --- Showing Sample Data ---
df_stats.sample(5)

Total  HP  Attack  Defense  Sp. Atk  Sp. Def  Speed    Type 1   Type 2
803    303  44      38       39       61       79     42     Fairy     None
892    476  75      70       70       98       70     93  Electric   Flying
206    525  80      82      100       83      100     80     Grass     None
508    224  40      29       45       29       45     36       Bug     None
414    458  73     100       60      100       60     65    Poison     None

### 3.2 | Variables

In [13]:
# --- Figure Variables ---
# Figure Size
logo_size = 0.087
wm_size = 0.1

# Variables
poke_url_clr = "https://static.wikia.nocookie.net/pokemon/images/"
angles = np.linspace(0, 2*np.pi, len(stats_label), endpoint=False)
angles = np.concatenate((angles, [angles[0]]))
folder_path_s01e04 = "s01e04_png"
png_name2_s01e04 = "data_slices_s01e04_spiderplotpokemon"

# Figure & Highlight Props
txt_kw = dict(fontsize=5.5, fontname=font_alt)
fig_text_prop = dict(ha="left", va="bottom")
subtitle_highlight_prop = [
    {"color": color_highlight1, "weight": "bold", "font": font_alt}
    , {"color": color_highlight2, "weight": "bold", "font": font_alt}
]
sources_highlight_prop = [
    {"font": font_main, "weight": "bold", "style": "normal", "fontsize": 6}
]

### 3.3 | Functions

In [14]:
# --- Func: Getting Color Pokemon Icon ---
def pokemon_icon_clr(idx):
    
    # --- Get Colored Icon ---
    icon_url_clr = df_icon_url["icon_url_clr"][idx]
    complete_url_clr = f"{poke_url_clr}{icon_url_clr}_HOME.png"
    
    poke_icon_clr = Image.open(urllib.request.urlopen(complete_url_clr))
    
    return poke_icon_clr

# --- Func: Getting Pokemon Icon (png) ---
def pokemon_icon(idx):
    
    # --- Get png Icon ---
    icon_url_blk = df_icon_url["icon_url_blk"].iloc[idx]
    poke_icon = Image.open(urllib.request.urlopen(f"{poke_url}{icon_url_blk}.png")).convert("LA")
    
    return poke_icon

In [15]:
# --- Func: Creating Spiderplot ---
def spiderplot_figure(ax, df_filter, poke_type, color, poke_icon, poke_icon_clr):

    # --- Avg., Min., Max. Total ---
    avg_total = df_filter["Total"].mean()
    min_total = df_filter["Total"].min()
    max_total = df_filter["Total"].max()

    # --- Average Number of Each Metrics (in List) ---
    avg_metrics_list = df_filter.loc[:, df_filter.columns != "Total"].select_dtypes(exclude="object").mean().T.to_list()
    avg_metrics_list = np.concatenate((avg_metrics_list, [avg_metrics_list[0]]))
    
    # --- Polar Figure Settings ---
    ax.set_theta_offset(np.pi / 2)
    ax.set_theta_direction(-1)
    ax.set_ylim(0, 160)
    ax.set_yticklabels([])

    # --- Plotting the Avg. Metrics ---
    ax.plot(angles, avg_metrics_list, "o--", color=color, label="Fire", linewidth=1)
    ax.fill(angles, avg_metrics_list, alpha=0.1, color=color)
    
    # --- Adjustment for X Label Position ---
    for label, angle in zip(ax.get_xticklabels(), angles):
        if angle in [np.pi, 0.0]:
            ha_alignment = "center"
        if 0 < angle < np.pi:
            ha_alignment = "left"
        if angle > np.pi:
            ha_alignment = "right"
        label.set_horizontalalignment(ha_alignment)
        label.set_verticalalignment("baseline")
        label.set_fontweight(500)
        
    # --- Set Metrics Label Category ---
    ax.set_thetagrids(angles[:-1]*180/np.pi, stats_label)
    ax.tick_params(axis="x", labelsize=8.5)

    # --- Annotation Avg. Metrics ---
    for angle, value in zip(angles, avg_metrics_list):
        va_alignment = "baseline"
        if angle in [np.pi, 0.0]:
            ha_alignment = "center"
            if angle in [np.pi]: va_alignment = "top"
            elif angle in [0.0]: va_alignment = "bottom"
        if 0 < angle < np.pi:
            ha_alignment = "left"
        if angle > np.pi:
            ha_alignment = "right"
        ann_txt = ax.text(angle, value+12, str(round(value, 1)), ha=ha_alignment, va=va_alignment, **txt_kw)
        ann_txt.set_path_effects([path_effects.Stroke(linewidth=1, foreground="white"), path_effects.Normal()])

    # --- Spine & Grid Color ---
    ax.spines["polar"].set_color(clr_spine_sp)

    # --- Title ---
    # Logo (Black Pokemon Icon)
    axlogo = ax.inset_axes([-0.3, 1.35, 0.15, 0.15], fc="None")
    axlogo.imshow(poke_icon)
    axlogo.axis("off")

    # Text (Pokemon Type & Totals)
    axtxt = ax.inset_axes([-0.09, 1.35, 0.15, 0.15], fc="None")
    ax_text(x=0, y=1.17, ax=axtxt, ha="left", size=9, weight="bold"
            , s=f"{poke_type}\n<Min. Total: ><{min_total}> <|> <Avg. Total: ><{round(avg_total, 1)}> <|> <Max. Total: ><{max_total}>"
            , highlight_textprops=[
                {"bbox": {"edgecolor": "grey", "facecolor": "grey", "pad": 0.5}, "weight": 500, "color": "white", "size": 6, "font": font_alt}
                , {"bbox": {"edgecolor": "grey", "facecolor": "grey", "pad": 0.5}, "weight": "bold", "color": "white", "size": 6, "font": font_alt}
                , {"color": face_color}
                , {"bbox": {"edgecolor": color, "facecolor": color, "pad": 0.5}, "weight": 500, "color": "white", "size": 6, "font": font_alt}
                , {"bbox": {"edgecolor": color, "facecolor": color, "pad": 0.5}, "weight": "bold", "color": "white", "size": 6, "font": font_alt}
                , {"color": face_color}
                , {"bbox": {"edgecolor": "black", "facecolor": "black", "pad": 0.5}, "weight": 500, "color": "white", "size": 6, "font": font_alt}
                , {"bbox": {"edgecolor": "black", "facecolor": "black", "pad": 0.5}, "weight": "bold", "color": "white", "size": 6, "font": font_alt}
            ])
    axtxt.axis("off")

    # --- Set Image Background (Colored Pokemon Icon) ---
    axbckg = ax.inset_axes([0, 0, 1, 1], polar=False, zorder=-10)
    axbckg.imshow(poke_icon_clr, alpha=0.1)
    axbckg.spines[["right", "left", "bottom", "top"]].set_visible(False)
    axbckg.xaxis.set_tick_params(labelbottom=False)
    axbckg.yaxis.set_tick_params(labelleft=False)
    axbckg.set_xticks([])
    axbckg.set_yticks([])
    
    return None

In [16]:
# --- Func: Generating Full Figure ---
def pokemon_stats(df):

    # --- Figure Size ---
    fig, axes = plt.subplots(figsize=(9.5, 18), ncols=3, nrows=6, subplot_kw=dict(polar=True))
    
    for ax, type in tqdm(zip(axes.flat, enumerate(type_list)), desc="🔃🕷️ Generating Spiderplot..."):

        # --- Variables ---
        idx, poke_type = type[0], type[1]
        poke_icon, poke_icon_clr = pokemon_icon(idx), pokemon_icon_clr(idx)
        time.sleep(7) # Prevent timeout when getting icons
        color_stats = df_icon_url["colors"][idx]

        # --- Filtering Dataframe ---
        df_filter = df.loc[df["Type 1"] == poke_type].drop(["Type 1", "Type 2"], axis=1).reset_index(drop=True)
        
        # --- Generate Spider Plots ---
        spiderplot_figure(ax=ax, df_filter=df_filter, poke_type=poke_type, color=color_stats, poke_icon=poke_icon, poke_icon_clr=poke_icon_clr)

    # --- Image Logo ---
    # Logo
    logo_ax = fig.add_axes([0.84, 0.96, logo_size, logo_size], fc="None")
    logo_ax.imshow(data_slices_logo)
    logo_ax.axis("off")

    # Watermark
    wm_ax = fig.add_axes([0.395, -0.09, wm_size, wm_size], fc="None")
    wm_ax.imshow(data_slices_wm)
    wm_ax.axis("off")

    # --- Figure Texts ---
    # Title
    fig_text(s="Elemental Insights: Pokémon Type Average and Total Base Stats", x=-0.025, y=1, fontsize=16, weight=800, **fig_text_prop)

    # Subtitle
    fig_text(s=f"Visualizing the <average and total base stats of each Pokémon type> | Data Scraped from <Pokemon Wiki>."
             , x=-0.025, y=0.99, fontsize=9, font=font_alt, highlight_textprops=subtitle_highlight_prop, **fig_text_prop)

    # References
    fig_text(s="""
    <Sources & Inspiration:>
    ∙ https://www.reddit.com/r/dataisbeautiful/comments/9je7st/how_to_stereotype_pokemon_stat_distributions_by/
    ∙ https://stackoverflow.com/questions/75845271/adding-an-image-background-to-a-radar-chart
    ∙ https://pokemon.fandom.com/wiki/Types
    """, x=-0.05, y=-0.05, fontsize=5, font=font_alt, style="italic", highlight_textprops=sources_highlight_prop, **fig_text_prop)
    
    # --- Finalizing Figure ---
    plt.tight_layout()
    plt.subplots_adjust(left=-0.05, hspace=1)
    plt.savefig(f"{folder_path_s01e04}/spiderplot/{png_name2_s01e04}.png"
                , dpi=figure_dpi_hd, bbox_inches="tight", edgecolor="none", transparent=False);

# --- Generate Spiderplot Figure ---
time.sleep(10)
pokemon_stats(df=df_stats)

🔃🕷️ Generating Spiderplot...: 18it [03:32, 11.80s/it]


<hr>
<center>
    <span style="font-family: Segoe UI; font-style: italic; font-weight: 700; font-size: 11px; padding: 7px; text-align: center; line-height: 1.2;"><u>Support me on:</u></span><br>
<!-- Hello world 👋. Thank you so much for downloading/forking my codes/works. If you like my work, please support me by giving stars (⭐) to this repo. You can also support me by donating to my Ko-Fi page ☕: https://ko-fi.com/caesarmario. Your donation and support will be highly appreciated since they motivate me to create new content. Thank you so much, and have a great day 😆👍. More about me: https://linktr.ee/caesarmario_ -->
    <span style="margin: 0; text-align: center; justify-content: center; align-items: center;">
        <a href='https://ko-fi.com/D1D3JU963' target='_blank'><img src='https://ko-fi.com/img/githubbutton_sm.svg' alt='Support me on Ko-fi Button'/></a></span><br>
<!-- Hello world 👋. Thank you so much for downloading/forking my codes/works. If you like my work, please support me by giving stars (⭐) to this repo. You can also support me by donating to my Ko-Fi page ☕: https://ko-fi.com/caesarmario. Your donation and support will be highly appreciated since they motivate me to create new content. Thank you so much, and have a great day 😆👍. More about me: https://linktr.ee/caesarmario_ -->
    <span style="font-family: Segoe UI; font-style: italic; font-weight: 700; font-size: 11px; padding: 7px; text-align: center; line-height: 1.2;"><u>Follow me in other platform:</u></span><br>
    <div align="center" style="margin: 0; padding: 10px; text-align: center; justify-content: center; align-items: center;">
        <ul style="list-style: none;">
<!-- Hello world 👋. Thank you so much for downloading/forking my codes/works. If you like my work, please support me by giving stars (⭐) to this repo. You can also support me by donating to my Ko-Fi page ☕: https://ko-fi.com/caesarmario. Your donation and support will be highly appreciated since they motivate me to create new content. Thank you so much, and have a great day 😆👍. More about me: https://linktr.ee/caesarmario_ -->
            <li style="margin: 0 20px 20px 0; vertical-align: top; list-style: none outside none; display: inline-block;"><a style="position: relative;" href="https://www.kaggle.com/caesarmario"><img style="width: 25px;" src="https://i.ibb.co/fnBbFZZ/kaggle-black.png"></a></li>
            <li style="margin: 0 20px 20px 0; vertical-align: top; list-style: none outside none; display: inline-block;"><a style="position: relative;" href="https://public.tableau.com/app/profile/caesarmario"><img style="width: 25px;" src="https://i.ibb.co/MkGtVv0/tableau-public-black.png"></a></li>
            <li style="margin: 0 20px 20px 0; vertical-align: top; list-style: none outside none; display: inline-block;"><a style="position: relative;" href="https://github.com/caesarmario"><img style="width: 25px;" src="https://i.ibb.co/d4ngSJk/github-black.png"></a></li>
<!-- Hello world 👋. Thank you so much for downloading/forking my codes/works. If you like my work, please support me by giving stars (⭐) to this repo. You can also support me by donating to my Ko-Fi page ☕: https://ko-fi.com/caesarmario. Your donation and support will be highly appreciated since they motivate me to create new content. Thank you so much, and have a great day 😆👍. More about me: https://linktr.ee/caesarmario_ -->
            <li style="margin: 0 20px 20px 0; vertical-align: top; list-style: none outside none; display: inline-block;"><a style="position: relative;" href="https://caesarmario.medium.com/"><img style="width: 25px;" src="https://i.ibb.co/8P7JfHx/medium-black.png"></a></li>
            <li style="margin: 0 20px 20px 0; vertical-align: top; list-style: none outside none; display: inline-block;"><a style="position: relative;" href="https://www.linkedin.com/in/caesarmario"><img style="width: 25px;" src="https://i.ibb.co/BwV3SH6/linkedin-black.png"></a></li>
            <li style="margin: 0 20px 20px 0; vertical-align: top; list-style: none outside none; display: inline-block;"><a style="position: relative;" href="https://twitter.com/caesarmario_"><img style="width: 25px;" src="https://i.ibb.co/Tb6Vwxh/twitter-black.png"></a></li>
        </ul>
    </div>
<!-- Hello world 👋. Thank you so much for downloading/forking my codes/works. If you like my work, please support me by giving stars (⭐) to this repo. You can also support me by donating to my Ko-Fi page ☕: https://ko-fi.com/caesarmario. Your donation and support will be highly appreciated since they motivate me to create new content. Thank you so much, and have a great day 😆👍. More about me: https://linktr.ee/caesarmario_ -->
    <img src="https://i.ibb.co/jZh1X6d/WM-2024-caesarmario.png" width=65% alt="WM">
</center>
<!-- Hello world 👋. Thank you so much for downloading/forking my codes/works. If you like my work, please support me by giving stars (⭐) to this repo. You can also support me by donating to my Ko-Fi page ☕: https://ko-fi.com/caesarmario. Your donation and support will be highly appreciated since they motivate me to create new content. Thank you so much, and have a great day 😆👍. More about me: https://linktr.ee/caesarmario_ -->